## Mean-Reversion Strategy (using Bollinger Bands)

Importing dependencies

In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from plotly.subplots import make_subplots

Fetching the data source and converting to pandas dataframe

In [2]:
data = pd.read_csv(filepath_or_buffer='../../resources/intraday.csv', parse_dates=['time'], index_col='time')

Getting details about the asset data by analysing the dataframe

In [3]:
data.head(10)

Close
time                
2009-12-31  1.432706
2010-01-01  1.438994
2010-01-04  1.442398
2010-01-05  1.436596
2010-01-06  1.440403
2010-01-07  1.431803
2010-01-08  1.441109
2010-01-11  1.451126
2010-01-12  1.447660
2010-01-13  1.452391

In [4]:
data.tail(10)

Close
time                
2021-12-20  1.124354
2021-12-21  1.127752
2021-12-22  1.128757
2021-12-23  1.132888
2021-12-24  1.132734
2021-12-27  1.132426
2021-12-28  1.133003
2021-12-29  1.131478
2021-12-30  1.136015
2021-12-31  1.132503

In [5]:
data.Close.to_frame()

Close
time                
2009-12-31  1.432706
2010-01-01  1.438994
2010-01-04  1.442398
2010-01-05  1.436596
2010-01-06  1.440403
...              ...
2021-12-27  1.132426
2021-12-28  1.133003
2021-12-29  1.131478
2021-12-30  1.136015
2021-12-31  1.132503

[3127 rows x 1 columns]

Getting more statistical insight into the dataset

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 3127 entries, 2009-12-31 to 2021-12-31
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Close   3127 non-null   float64
dtypes: float64(1)
memory usage: 48.9 KB


In [7]:
data.describe()

Close
count  3127.000000
mean      1.219630
std       0.107936
min       1.039047
25%       1.124366
50%       1.190079
75%       1.317046
max       1.484406

Since the only attribute we need is closing price
we modify the data frame


In [8]:
data = data.Close.to_frame()

In [9]:
data.head(10)

Close
time                
2009-12-31  1.432706
2010-01-01  1.438994
2010-01-04  1.442398
2010-01-05  1.436596
2010-01-06  1.440403
2010-01-07  1.431803
2010-01-08  1.441109
2010-01-11  1.451126
2010-01-12  1.447660
2010-01-13  1.452391

We plot the closing price of our asset

In [10]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [11]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

We proceed to define baseline and compute returns !needs improvement!

In [12]:
data['returns'] = np.log(data.div(data.shift(1)))

In [13]:
data

Close   returns
time                          
2009-12-31  1.432706       NaN
2010-01-01  1.438994  0.004379
2010-01-04  1.442398  0.002363
2010-01-05  1.436596 -0.004031
2010-01-06  1.440403  0.002647
...              ...       ...
2021-12-27  1.132426 -0.000272
2021-12-28  1.133003  0.000510
2021-12-29  1.131478 -0.001347
2021-12-30  1.136015  0.004002
2021-12-31  1.132503 -0.003097

[3127 rows x 2 columns]

Defining Mean-Reversion

In [14]:
SMA = 30
dev = 2

In [15]:
data['SMA'] = data['Close'].rolling(SMA).mean()

We try to visualise the asset price and SMA together

In [16]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Viewing a shorter time interval for the asset

In [17]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Plotting the standard deviation to assess risk of asset

In [18]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data['Close'].rolling(SMA).std(), name='Close'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Volatility')

fig.show()

Since we want to incorporate bollinger bands we compute it

In [19]:
data['Lower'] = data['SMA'] - data['Close'].rolling(SMA).std() * dev
data['Upper'] = data['SMA'] + data['Close'].rolling(SMA).std() * dev

In [20]:
data

Close   returns       SMA     Lower     Upper
time                                                        
2009-12-31  1.432706       NaN       NaN       NaN       NaN
2010-01-01  1.438994  0.004379       NaN       NaN       NaN
2010-01-04  1.442398  0.002363       NaN       NaN       NaN
2010-01-05  1.436596 -0.004031       NaN       NaN       NaN
2010-01-06  1.440403  0.002647       NaN       NaN       NaN
...              ...       ...       ...       ...       ...
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067

[3127 rows x 5 columns]

In [21]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.index, y=data.Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.index, y=data.Upper, name='Upper'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [22]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Upper, name='Upper'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

Dropping NaN values

In [23]:
data.dropna(inplace=True)

In [24]:
data

Close   returns       SMA     Lower     Upper
time                                                        
2010-02-10  1.375327 -0.002093  1.415322  1.360071  1.470573
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788
...              ...       ...       ...       ...       ...
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067

[3098 rows x 5 columns]

In [25]:
data['distance'] = data.Close - data.SMA

In [26]:
data['position'] = np.where(data.Close < data.Lower, 1, np.nan)
data['position'] = np.where(data.Close > data.Upper, -1, data['position'])

In [27]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-10  1.375327 -0.002093  1.415322  1.360071  1.470573 -0.039995   
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  
time                  
2010-02-10       NaN  
2010-02-11       NaN  
2010-02-12       NaN  
2010-02-15       NaN  
2010-02-16       NaN  
...              ...  
2021-12-27       NaN  
2021-12-28       NaN  
2021-12-29       NaN  
2021-12-30       NaN  
2021-12-31       NaN  

[3098 rows x 7 columns]

In [28]:
data['position'] = np.where(data.distance * data.distance.shift(1) < 0, 0, data['position'])

In [29]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-10  1.375327 -0.002093  1.415322  1.360071  1.470573 -0.039995   
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  
time                  
2010-02-10       NaN  
2010-02-11       NaN  
2010-02-12       NaN  
2010-02-15       NaN  
2010-02-16       NaN  
...              ...  
2021-12-27       NaN  
2021-12-28       NaN  
2021-12-29       NaN  
2021-12-30       NaN  
2021-12-31       NaN  

[3098 rows x 7 columns]

In [30]:
data.position = data.position.ffill().fillna(0)

In [31]:
data.position.value_counts()

 0.0    1404
 1.0     907
-1.0     787
Name: position, dtype: int64

IMPROVE

In [32]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(go.Scatter(x=data.index, y=data.Close, name='Close'))
fig.add_trace(go.Scatter(x=data.index, y=data.SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.index, y=data.Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.index, y=data.Upper, name='Upper'))
fig.add_trace(go.Scatter(x=data.index, y=data.position, name='Position'), secondary_y=True)

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [33]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Close, name='Close'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].SMA, name=f'SMA - {SMA}'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Lower, name='Lower'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].Upper, name='Upper'))
fig.add_trace(go.Scatter(x=data.loc['2018'].index, y=data.loc['2018'].position, name='Position'), secondary_y=True)

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [34]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-10  1.375327 -0.002093  1.415322  1.360071  1.470573 -0.039995   
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  
time                  
2010-02-10       0.0  
2010-02-11       0.0  
2010-02-12       0.0  
2010-02-15       0.0  
2010-02-16       0.0  
...              ...  
2021-12-27       0.0  
2021-12-28       0.0  
2021-12-29       0.0  
2021-12-30       0.0  
2021-12-31       0.0  

[3098 rows x 7 columns]

We describe strategy and compute returns with the strategy

In [35]:
data['strategy'] = data.position.shift(1) * data['returns']

In [36]:
data.dropna(inplace=True)

In [37]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857 -0.042572   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  strategy  
time                            
2010-02-11       0.0      -0.0  
2010-02-12       0.0      -0.0  
2010-02-15       0.0      -0.0  
2010-02-16       0.0       0.0  
2010-02-17       0.0      -0.0  
...              ...       ...  
2021-12-27       0.0      -0.0  
2021-12-28       0.0       0.0  
2021-12-29       0.0      -0.0  
2021-12-30       0.0       0.0  
2021-12-31       0.0      -0.0  

[3097 rows x 8 columns]

In [38]:
data['creturns'] = data['returns'].cumsum().apply(np.exp)

In [39]:
data['cstrategy'] = data['strategy'].cumsum().apply(np.exp)

In [40]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.index, y=data.creturns, name='Returns (Baseline)'))
fig.add_trace(go.Scatter(x=data.index, y=data.cstrategy, name='Returns (Strategy)'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [41]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857 -0.042572   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  strategy  creturns  cstrategy  
time                                                 
2010-02-11       0.0      -0.0  0.994801   1.000000  
2010-02-12       0.0      -0.0  0.991396   1.000000  
2010-02-15       0.0      -0.0  0.989077   1.000000  
2010-02-16       0.0       0.0  1.001005   1.000000  
2010-02-17       0.0      -0.0  0.989359   1.000000  
...              ...       ...       ...        ...  
2021-12-27       0.0      -0.0  0.823387   0.951087  
2021-12-28       0.0       0.0  0.823807   0.951087  
2021-12-29       0.0      -0.0  0.822697   0.951087  
2021-12-30       0.0       0.0  0.825997   0.951087  
2021-12-31       0.0      -0.0  0.823443   0.951087  

[3097 rows x 10 columns]

Taking trading costs into consideration

In [42]:
ptc = 0.00007

In [43]:
data['trades'] = data.position.diff().fillna(0).abs()

In [44]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857 -0.042572   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  strategy  creturns  cstrategy  trades  
time                                                         
2010-02-11       0.0      -0.0  0.994801   1.000000     0.0  
2010-02-12       0.0      -0.0  0.991396   1.000000     0.0  
2010-02-15       0.0      -0.0  0.989077   1.000000     0.0  
2010-02-16       0.0       0.0  1.001005   1.000000     0.0  
2010-02-17       0.0      -0.0  0.989359   1.000000     0.0  
...              ...       ...       ...        ...     ...  
2021-12-27       0.0      -0.0  0.823387   0.951087     0.0  
2021-12-28       0.0       0.0  0.823807   0.951087     0.0  
2021-12-29       0.0      -0.0  0.822697   0.951087     0.0  
2021-12-30       0.0       0.0  0.825997   0.951087     0.0  
2021-12-31       0.0      -0.0  0.823443   0.951087     0.0  

[3097 rows x 11 columns]

In [45]:
data.trades.value_counts()

0.0    2937
1.0     160
Name: trades, dtype: int64

In [46]:
data['strategy_net'] = data.strategy - data.trades * ptc

In [47]:
data['cstrategy_net'] = data.strategy_net.cumsum().apply(np.exp)

In [48]:
data

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602 -0.044995   
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857 -0.042572   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  strategy  creturns  cstrategy  trades  strategy_net  \
time                                                                        
2010-02-11       0.0      -0.0  0.994801   1.000000     0.0          -0.0   
2010-02-12       0.0      -0.0  0.991396   1.000000     0.0          -0.0   
2010-02-15       0.0      -0.0  0.989077   1.000000     0.0          -0.0   
2010-02-16       0.0       0.0  1.001005   1.000000     0.0           0.0   
2010-02-17       0.0      -0.0  0.989359   1.000000     0.0          -0.0   
...              ...       ...       ...        ...     ...           ...   
2021-12-27       0.0      -0.0  0.823387   0.951087     0.0          -0.0   
2021-12-28       0.0       0.0  0.823807   0.951087     0.0           0.0   
2021-12-29       0.0      -0.0  0.822697   0.951087     0.0          -0.0   
2021-12-30       0.0       0.0  0.825997   0.951087     0.0           0.0   
2021-12-31       0.0      -0.0  0.823443   0.951087     0.0          -0.0   

            cstrategy_net  
time                       
2010-02-11       1.000000  
2010-02-12       1.000000  
2010-02-15       1.000000  
2010-02-16       1.000000  
2010-02-17       1.000000  
...                   ...  
2021-12-27       0.940495  
2021-12-28       0.940495  
2021-12-29       0.940495  
2021-12-30       0.940495  
2021-12-31       0.940495  

[3097 rows x 13 columns]

We plot returns with and without trading costs

In [49]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].creturns, name='Returns (Baseline)'))
fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].cstrategy, name='Returns (Strategy)'))
fig.add_trace(go.Scatter(x=data.loc['2018':].index, y=data.loc['2018':].cstrategy_net, name='Returns (Strategy + trading costs)'))

fig.update_layout(title='EUR/USD', xaxis_title='Time', yaxis_title='Price')

fig.show()

In [50]:
data[['returns', 'strategy_net']].mean() * (252)

returns        -0.015807
strategy_net   -0.004992
dtype: float64

In [51]:
data[['returns', 'strategy_net']].std() * np.sqrt(252)

returns         0.086856
strategy_net    0.065438
dtype: float64

Now we make use of a comprehensive backtester which implements Mean-Reversion with Bollinger Bands and optimize our parameters to maximize returns

In [52]:
from MeanReversionBacktester import MeanReversionBacktester as MRB

In [53]:
testMRB = MRB(symbol='EUR/USD', SMA=30, dev=2, start='2010', end='2021', tc=0.00007)

In [54]:
testMRB

MeanReversionBacktester(symbol = EUR/USD, SMA = 30, dev = 2, start = 2010, end = 2021, tc=7e-05)

In [55]:
testMRB.data

Close   returns       SMA     Lower     Upper
time                                                        
2010-02-11  1.368176 -0.005213  1.413171  1.355739  1.470602
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857
...              ...       ...       ...       ...       ...
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067

[3097 rows x 5 columns]

In [56]:
testMRB.test_strategy()

(0.951087, 0.123341)

In [57]:
testMRB.results

Close   returns       SMA     Lower     Upper  distance  \
time                                                                     
2010-02-12  1.363494 -0.003428  1.410654  1.351320  1.469989 -0.047160   
2010-02-15  1.360304 -0.002342  1.407918  1.347088  1.468748 -0.047614   
2010-02-16  1.376709  0.011988  1.405922  1.345055  1.466788 -0.029213   
2010-02-17  1.360692 -0.011702  1.403264  1.341672  1.464857 -0.042572   
2010-02-18  1.346149 -0.010746  1.400409  1.336397  1.464421 -0.054261   
...              ...       ...       ...       ...       ...       ...   
2021-12-27  1.132426 -0.000272  1.129582  1.121492  1.137672  0.002844   
2021-12-28  1.133003  0.000510  1.129461  1.121708  1.137214  0.003542   
2021-12-29  1.131478 -0.001347  1.129439  1.121713  1.137166  0.002038   
2021-12-30  1.136015  0.004002  1.129569  1.121532  1.137607  0.006446   
2021-12-31  1.132503 -0.003097  1.129425  1.121782  1.137067  0.003078   

            position  strategy  trades  strategy_net  creturns  cstrategy  \
time                                                                        
2010-02-12       0.0      -0.0     0.0          -0.0  0.996578   1.000000   
2010-02-15       0.0      -0.0     0.0          -0.0  0.994246   1.000000   
2010-02-16       0.0       0.0     0.0           0.0  1.006237   1.000000   
2010-02-17       0.0      -0.0     0.0          -0.0  0.994530   1.000000   
2010-02-18       0.0      -0.0     0.0          -0.0  0.983900   1.000000   
...              ...       ...     ...           ...       ...        ...   
2021-12-27       0.0      -0.0     0.0          -0.0  0.827690   0.951087   
2021-12-28       0.0       0.0     0.0           0.0  0.828112   0.951087   
2021-12-29       0.0      -0.0     0.0          -0.0  0.826997   0.951087   
2021-12-30       0.0       0.0     0.0           0.0  0.830313   0.951087   
2021-12-31       0.0      -0.0     0.0          -0.0  0.827746   0.951087   

            cstrategy_net  
time                       
2010-02-12       1.000000  
2010-02-15       1.000000  
2010-02-16       1.000000  
2010-02-17       1.000000  
2010-02-18       1.000000  
...                   ...  
2021-12-27       0.940495  
2021-12-28       0.940495  
2021-12-29       0.940495  
2021-12-30       0.940495  
2021-12-31       0.940495  

[3096 rows x 13 columns]

We find the number of trades made

In [58]:
testMRB.results.trades.value_counts()

0.0    2936
1.0     160
Name: trades, dtype: int64

In [59]:
testMRB.plot_results()

We give a set of boundaries to optimize our parameters within

SMA_range describes the range of days over which the simple moving average must be taken

dev_range describes the range of standard deviations we need to describe the bollinger bands within

In [60]:
SMA_range = (10, 150)
dev_range = (1, 3)

In [61]:
testMRB.optimize_parameters(SMA_range=SMA_range, dev_range=dev_range)

((10, 1), 1.448158)

In [62]:
testMRB.test_strategy()

(1.448158, 0.611941)

Set of parameters which give maximum returns and a plot of returns for the same

In [63]:
testMRB.plot_results()

In [64]:
#Return
testMRB.results[['returns', 'strategy_net']].mean() * (252)

returns        -0.014601
strategy_net    0.026657
dtype: float64

In [65]:
#Risk
testMRB.results[['returns', 'strategy_net']].std() * np.sqrt(252)

returns         0.086713
strategy_net    0.073317
dtype: float64